(generator)=
# generator
A hydropower generating unit consisting of a hydropower turbine and a generator which uses falling water to generate electricity

|   |   |
|---|---|
|Input connections|{ref}`plant`, {ref}`needle_combination`, {ref}`reserve_group`, {ref}`commit_group`, {ref}`busbar`, {ref}`gen_reserve_capability`|
|Output connections|{ref}`plant`, {ref}`reserve_group`, {ref}`commit_group`, {ref}`needle_combination`, {ref}`busbar`, {ref}`gen_reserve_capability`|
|License|SHOP_OPEN|
|Release version|13.0.0.a|

```{contents}
:local:
:depth: 1
```

## Introduction
The generator object is one of the most fundamental building blocks in any SHOP model. The generator represents the combination of a generator and turbine, which is why attributes such as the [generator efficiency](generator:gen_eff_curve) and the [turbine efficiency](generator:turb_eff_curves) are both located on the generator object. The fundamental equation that governs the generation of electricity from flowing water is handled on the generator level in SHOP:

```{math}
p = \rho \cdot g \cdot h \cdot q \cdot \eta_{gen}(p) \cdot \eta_{turb}(q, h),
```

where $p$ is the power, $\rho$ is the density of water, $g$ is the acceleration due to gravity, $h$ is the effective head of the generator, $q$ is the flow of water through the turbine, $\eta_{gen}$ is the efficiency of the generator and $\eta_{turb}$ is the efficiency of the turbine. See the [PQ curve tutorial](pq-tutorial) for more details on how this relationship is handled by SHOP.

## Required input
A generator must always be connected to a [](plant) object, and the plant object is then connected to reservoirs/tunnels/rivers/etc upstream and downstream. The [penstock number](generator:penstock) is required to specify which of the penstocks in the plant the generator is connected to, since each penstock has its own [loss coefficient](plant:penstock_loss) and could be shared between several units. The operating range of the generator must also be specified. The rated static [minimum production](generator:p_min) and [maximum production](generator:p_max) must be defined to set the legal production range of the generator. The [nominal production](generator:p_nom) should also be specified, but is only used for droop calculations when the generator delivers [FCR reserves](reserves). The legal discharge range for the generator is defined through the highest and lowest discharge points in the [turbine efficiency curves](generator:turb_eff_curves) for the given effective head in each hour in the optimization. Since the turbine efficiency is head dependent, the discharge limits are also head dependent.

## Pelton turbines
Pelton turbines have different operating characteristics compared to Francis and Kaplan turbines. The production and discharge limits of Pelton turbines are determined by which combination of needles are used to push water through the nozzle. This can be modelled in SHOP by connecting several [](needle_combination) objects to the generator. The input attributes [p_min](needle_combination:p_min), [p_max](needle_combination:p_max), [p_nom](needle_combination:p_nom), and [turb_eff_curves](needle_combination:turb_eff_curves) on each needle_combination will determine the operating ranges, and SHOP will optimize which needle_combination will be used in each time step of the optimization. Please see the [Pelton example](pelton) for more modelling details. 

## Generators with forbidden operating regions
The Pelton functionality can also be used to model Francis and Kaplan turbines with forbidden operating regions. This is discussed in the [Pelton example](pelton).

## Reversible turbines
Some turbines can be reversed and operated as pumps, either as a single pump-turbine machine or as a ternary set of one turbine and one pump. Both of these types of reversible turbines are modelled in SHOP as two separate generator and [](pump) objects located in the same power plant. If the reversible turbine is a single machine that cannot produce and consume power at the same time, two [](commit_group) objects must be used to ensure that the generator and pump never operate at the same time. The [reversible turbine example](reversible-turbine-example) shows how this is done in practice. Ternary sets that can run in hydraulic short circuit do not require any commit_group modelling. 

## Reserve capacity
Many of the attributes on the generator object are related to the delivery of different types of reserve capacity. To be able to deliver reserve capacity, a generator must either: have defined a fixed reserve schedule (such as [frr_up_schedule](generator:frr_up_schedule)), be connected to a [](reserve_group) object with a reserve obligation (such as [frr_up_obligation](reserve_group:frr_up_obligation)), or be connected to a reserve_group that is itself connected to a reserve capacity [](market). The [reserve tutorial](reserves) gives an overview of the reserve functionality in SHOP, and several examples are related to this topic. The [reserve obligation example](reserve-example) shows how generators cooperate to optimally distribute the reserve obligation defined in the reserve_groups.

## Unit commitment
The unit commitment decision is the choice of whether a unit should be on or off. This decision is part of the optimization problem in SHOP in full iterations. When one changes to incremental iterations, the unit commitment decisions of all units in the system is locked to either on or off. This allows SHOP to refine the problem and accurately estimate head losses. However, the unit commitment decision is not simple to solve as it is non-convex, and accurate modelling comes with higher computational costs.

### Binary variables
Binary variables must be used to ensure that a generator is either off or operating within its legal limits. Otherwise, fractional starts with operation below minimum production and/or discharge may occur. In the realm of optimization, a binary variable can only take on the values of 0 or 1, while a regular variable is continuous between its upper and lower bound. The illustrative equations below shows how the binary variable $u$ constrains both the production variable $p$ and discharge variable $q$ of the generator. If $u = 0$, both $p$ and $q$ also have to be zero, while $u = 1$ constrain $p$ and $q$ to be within their operating limits:

```{math}
P^{min}\cdot u \leq p \leq P^{max}\cdot u \\
Q^{min}\cdot u \leq q \leq Q^{max}\cdot u
```

The default behaviour in SHOP is to relax this binary variable to be continuous between 0 and 1, which allows operation below $P^{min}$ and $Q^{min}$. This is due to the increased calculation time that is associated with binary variables and Mixed Integer Linear Programming (MILP). The [mip_flag](plant:mip_flag) attribute on the plant object can be used to specify when binary variables should be used instead of the relaxed default behaviour. It is typical to set the flag to 1 (active) for the first day(s) in the optimization horizon to get more accurate results closer to real time. Using binary variables is especially important for Pelton units that require one binary variable per needle_combination, and for generators that could deliver spinning reserve capacity (FCR and FRR).

### Fractional starts and cut-off limits
As mentioned earlier, the unit commitment decision must be made for all units in all time steps when switching from full to incremental iterations in SHOP. If binary variables have been used in a time step the full iterations, the unit commitment decision will be completely decided by the value of the binary variable. For time steps where the binary variables have been relaxed, the decision to turn on or off the unit is decided by the global [gen_turn_off_limit](global_settings:gen_turn_off_limit) or the generator-specific attribute [gen_turn_off_limit](generator:gen_turn_off_limit). The gen_turn_off_limit specifies how fractional the relaxed binary variable can be before the unit is considered off. The default value is 0.5, which means that the unit is considered off if $q$ is less than 50% of $Q^{min}$. Otherwise, the unit is considered on and must operate within its range in the following incremental iterations.

### Start and stop costs
Turning generators on and off is usually associated with some loss of water, wear and tear, and manual labour, and therefore a cost. For this to be reflected in the optimization and unit commitment decision, the attributes [startcost](generator:startcost) and [stopcost](generator:stopcost) can be set. These costs will be applied when the unit goes from off to on and vice versa. 

## Examples
  - [](best-profit)
  - [](best-profit-basic-example)
  - [](discrete-droop)
  - [](maintenance-example)
  - [](min_uptime_downtime)
  - [](reserve-example)
  - [](pelton)
  - [](reversible-turbine-example)
  - [](pq-example)
  

## References
  - An overview on formulations and optimization methods for the unit-based short-term hydro scheduling problem {cite}`Kong2020`
  - Dynamic incorporation of nonlinearity into MILP formulation for short-term hydro scheduling {cite}`Skjelbred2020`
  - A comparison of linear interpolation and spline interpolation for turbine efficiency curves in short-term hydropower scheduling problems {cite}`Zhang2019`
  - Calculation of power compensation for a pumped storage hydropower plant with hydraulic short-circuit operation {cite}`Skjelbred2017b`
  

## Attributes

In [1]:
from IPython.core.display import HTML
HTML("""<table id="generator-table" class="display compact"></table>
<script>
enableDataTable(
  "#generator-table",
  "/_static/data/generator-attribute-table.json"
);
</script>
""")

(generator:type)=
### type
Specification of type of generator when using ASCII-files as input. 0 indicates Francis or Kaplan turbine while PELTON indicates a pelton unit (or a unit where forbidden operating zones is modelled as pelton) (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:num_needle_comb)=
### num_needle_comb
Number of needle combinations for pelton units (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:prod_area)=
### prod_area
Future deprecation: use a busbar object per price area and connect the appropriate units and markets to the busbars. Production from this generator will be sold in markets connected to the given price area (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:initial_state)=
### initial_state
The initial operation state of the generator before the optimization period: -1 = not set; 0 = not running; 1 = running (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:penstock)=
### penstock
The penstock number the generator is connected to in the plant, must be a number between 1 and the size of the penstock_loss attribute on the plant object. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:separate_droop)=
### separate_droop
A flag to turn on (1) or off (0, default) the building of separate droop variables for FCR-N, FCR-D up, and FCR-D down for the generator. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:p_min)=
### p_min
Static minimum production for the generator (xUnit: MW, yUnit: MW)


(generator:p_max)=
### p_max
Static maximum production for the generator (xUnit: MW, yUnit: MW)


(generator:p_nom)=
### p_nom
The nominal production that is the rated capacity of the generator, only used in droop calculations (xUnit: MW, yUnit: MW)


(generator:gen_eff_curve)=
### gen_eff_curve
The generator efficiency curve as a function of the produced power (xUnit: MW, yUnit: %)


(generator:turb_eff_curves)=
### turb_eff_curves
The turbine efficiency curve(s) as a function of discharge through the turbine. Several curves can be specified for different head levels (reference value in the XY) to make the efficiency head-dependent. (xUnit: M3/S, yUnit: %)

<!-- Add content here -->
<!-- ### Testing -->
<!-- This is a test. -->
(generator:maintenance_flag)=
### maintenance_flag
Flag determining whether the generator is out for maintenance for a given time step (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:startcost)=
### startcost
Generator startup cost when turning on the unit in one time step (xUnit: NO_UNIT, yUnit: NOK)


(generator:stopcost)=
### stopcost
Generator shutdown cost when turning off the unit in one time step (xUnit: NO_UNIT, yUnit: NOK)


(generator:discharge_cost_curve)=
### discharge_cost_curve
Extra cost depending on the discharge of the generator (xUnit: M3/S, yUnit: NOK/H/M3/S)


(generator:priority)=
### priority
Time-dependent generators priority to define the uploading order among all the generators in a plant. Plant gen_priority will be ignored if generator priority is set. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:committed_in)=
### committed_in
Committed status given by the user used to define the operating status of the generator in the optimization: 0 - committed not to run; 1 - committed to run (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:committed_flag)=
### committed_flag
Flag determining whether the input commit status should be used for a given time step or not (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:min_p_constr)=
### min_p_constr
Time-dependent minimum production limit for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:min_p_constr_flag)=
### min_p_constr_flag
Flag determining whether the time-dependent minimum production limit for the generator should be included in the building of the original PQ curve (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:max_p_constr)=
### max_p_constr
Time-dependent maximum production limit for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:max_p_constr_flag)=
### max_p_constr_flag
Flag determining whether the time-dependent maximum production limit for the generator should be included in the building of the original PQ curve (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:min_q_constr)=
### min_q_constr
Time-dependent minimum discharge limit for the generator (xUnit: NO_UNIT, yUnit: M3/S)


(generator:min_q_constr_flag)=
### min_q_constr_flag
Flag determining whether the time-dependent minimum discharge limit for the generator should be included in the building of the original PQ curve (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:max_q_constr)=
### max_q_constr
Time-dependent maximum discharge limit for the generator (xUnit: NO_UNIT, yUnit: M3/S)


(generator:max_q_constr_flag)=
### max_q_constr_flag
Flag determining whether the time-dependent maximum discharge limit for the generator should be included in the building of the original PQ curve (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:max_q_limit_rsv_down)=
### max_q_limit_rsv_down
Maximum generator discharge limit (m3/s) and downstream reservoir water level (meter above sea level) relation (xUnit: METER, yUnit: M3/S)


(generator:upstream_min)=
### upstream_min
Minimum water level of upstream reservoir required for running the generator (xUnit: NO_UNIT, yUnit: METER)


(generator:upstream_min_flag)=
### upstream_min_flag
Flag determining whether the minimum water level of upstream reservoir required for running the generator should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:downstream_max)=
### downstream_max
Maximum water level of downstream reservoir allowed when running the generator (xUnit: NO_UNIT, yUnit: METER)


(generator:downstream_max_flag)=
### downstream_max_flag
Flag determining whether the maximum water level of downstream allowed when running the generator should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:production_schedule)=
### production_schedule
Generator production schedule. Note that setting a schedule higher or lower than the operating limits of the generator is allowed, but this might lead to inaccurate results due to lacking efficiency data (xUnit: NO_UNIT, yUnit: MW)


(generator:production_schedule_flag)=
### production_schedule_flag
Flag determining whether the generator production schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:discharge_schedule)=
### discharge_schedule
Generator discharge schedule. Note that setting a schedule higher or lower than the operating limits of the generator is allowed, but this might lead to inaccurate results due to lacking efficiency data (xUnit: NO_UNIT, yUnit: M3/S)


(generator:discharge_schedule_flag)=
### discharge_schedule_flag
Flag determining whether the generator discharge schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_mip_flag)=
### fcr_mip_flag
Flag determining whether binary variables should be used to indicate that the generator can contribute to FCR only if its unused capacity is no less than 2% of the maximum production limit (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:p_fcr_min)=
### p_fcr_min
Temporary minimum production for the generator when delivering FCR. If this is not set, the head-dpendent minimum production of the generator will be used instead. Note that the p_fcr_n_min and p_fcr_d_min attributes will take precedence over this attribute if both are specified (xUnit: NO_UNIT, yUnit: MW)


(generator:p_fcr_n_min)=
### p_fcr_n_min
Temporary minimum production for the generator when delivering FCR-N. If this attribute is not specified, the p_fcr_min attribute on the generator object will be used instead (xUnit: NO_UNIT, yUnit: MW)


(generator:p_fcr_d_min)=
### p_fcr_d_min
Temporary minimum production for the generator when delivering FCR-D. If this attribute is not specified, the p_fcr_min attribute on the generator object will be used instead (xUnit: NO_UNIT, yUnit: MW)


(generator:p_fcr_max)=
### p_fcr_max
Temporary maximum production for the generator when delivering FCR. If this is not set, the head-dpendent maximum production of the generator will be used instead. Note that the p_fcr_n_max and p_fcr_d_max attributes will take precedence over this attribute if both are specified (xUnit: NO_UNIT, yUnit: MW)


(generator:p_fcr_n_max)=
### p_fcr_n_max
Temporary maximum production for the generator when delivering FCR-N. If this attribute is not specified, the p_fcr_max attribute on the generator object will be used instead (xUnit: NO_UNIT, yUnit: MW)


(generator:p_fcr_d_max)=
### p_fcr_d_max
Temporary maximum production for the generator when delivering FCR-D. If this attribute is not specified, the p_fcr_max attribute on the generator object will be used instead (xUnit: NO_UNIT, yUnit: MW)


(generator:p_frr_min)=
### p_frr_min
Minimum production for the generator when delivering FRR. If not specified, the head-dependent minimum production for the generator (or needle_combination for pelton units) is used as lower bound for downward FRR (xUnit: NO_UNIT, yUnit: MW)


(generator:p_frr_max)=
### p_frr_max
Maximum production for the generator when delivering FRR. If not specified, the head-dependent maximum production for the generator (or needle_combination for pelton units) is used as upper bound for upward FRR (xUnit: NO_UNIT, yUnit: MW)


(generator:p_rr_min)=
### p_rr_min
Temporary minimum production for the generator when delivering RR (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_up_min)=
### frr_up_min
Minimum FRR_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_up_max)=
### frr_up_max
Maximum FRR_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_down_min)=
### frr_down_min
Minimum FRR_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_down_max)=
### frr_down_max
Maximum FRR_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_up_min)=
### fcr_n_up_min
Minimum FCR_N_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_up_max)=
### fcr_n_up_max
Maximum FCR_N_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_down_min)=
### fcr_n_down_min
Minimum FCR_N_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_down_max)=
### fcr_n_down_max
Maximum FCR_N_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_up_min)=
### fcr_d_up_min
Minimum FCR_D_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_up_max)=
### fcr_d_up_max
Maximum FCR_D_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_down_min)=
### fcr_d_down_min
Minimum FCR_D_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_down_max)=
### fcr_d_down_max
Maximum FCR_D_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_up_min)=
### rr_up_min
Minimum RR_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_up_max)=
### rr_up_max
Maximum RR_UP delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_down_min)=
### rr_down_min
Minimum RR_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_down_max)=
### rr_down_max
Maximum RR_DOWN delivery for the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_up_schedule)=
### fcr_n_up_schedule
Generator FCR_N_UP delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_up_schedule_flag)=
### fcr_n_up_schedule_flag
Flag determining whether the generator FCR_N_UP delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_n_down_schedule)=
### fcr_n_down_schedule
Generator FCR_N_DOWN delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_down_schedule_flag)=
### fcr_n_down_schedule_flag
Flag determining whether the generator FCR_N_DOWN delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_up_schedule)=
### fcr_d_up_schedule
Generator FCR_D_UP delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_up_schedule_flag)=
### fcr_d_up_schedule_flag
Flag determining whether the generator FCR_D_UP delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_down_schedule)=
### fcr_d_down_schedule
Generator FCR_D_DOWN delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_down_schedule_flag)=
### fcr_d_down_schedule_flag
Flag determining whether the generator FCR_D_DOWN delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:frr_up_schedule)=
### frr_up_schedule
Generator FRR_UP delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_up_schedule_flag)=
### frr_up_schedule_flag
Flag determining whether the generator FRR_UP delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:frr_down_schedule)=
### frr_down_schedule
Generator FRR_DOWN delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_down_schedule_flag)=
### frr_down_schedule_flag
Flag determining whether the generator FRR_DOWN delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:rr_up_schedule)=
### rr_up_schedule
Generator RR_UP delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_up_schedule_flag)=
### rr_up_schedule_flag
Flag determining whether the generator RR_UP delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:rr_down_schedule)=
### rr_down_schedule
Generator RR_DOWN delivery schedule (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_down_schedule_flag)=
### rr_down_schedule_flag
Flag determining whether the generator RR_DOWN delivery schedule should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:droop_cost)=
### droop_cost
The cost for the inverse unit droop when it is modelled as a variable in the optimization model, which makes SHOP prefer high droop settings. The default droop_cost on global_settings is used if this attribute is not specified (xUnit: NO_UNIT, yUnit: NOK)


(generator:fixed_droop)=
### fixed_droop
Fixed unit droop given as input data (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fixed_droop_flag)=
### fixed_droop_flag
Flag determining whether the fixed droop setting should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:droop_min)=
### droop_min
The lower bound of the unit droop when it is modelled as a variable in the optimization model. This bound is applied together with other FCR constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:droop_max)=
### droop_max
The upper bound of the unit droop when it is modelled as a variable in the optimization model. This bound is applied together with other FCR constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:discrete_droop_values)=
### discrete_droop_values
A list of all legal droop values for the generator. If the functionality for fixing the unit droop is activated by the 'set droop_discretization_limit' command, this list of discrete values will be used when fixing the generator droop (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_n_discrete_droop_values)=
### fcr_n_discrete_droop_values
A list of all legal droop values for FCR-N reserves when the generator is built with separate droop. If the functionality for fixing the unit droop is activated by the 'set droop_discretization_limit' command, this list of discrete values will be used when fixing the generator droop (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_up_discrete_droop_values)=
### fcr_d_up_discrete_droop_values
A list of all legal droop values for FCR-D up reserves when the generator is built with separate droop. If the functionality for fixing the unit droop is activated by the 'set droop_discretization_limit' command, this list of discrete values will be used when fixing the generator droop (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_down_discrete_droop_values)=
### fcr_d_down_discrete_droop_values
A list of all legal droop values for FCR-D down reserves when the generator is built with separate droop. If the functionality for fixing the unit droop is activated by the 'set droop_discretization_limit' command, this list of discrete values will be used when fixing the generator droop (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:reserve_ramping_cost_up)=
### reserve_ramping_cost_up
Upward reserve ramping cost for changing reserve delivery of the generator (xUnit: NO_UNIT, yUnit: NOK)


(generator:reserve_ramping_cost_down)=
### reserve_ramping_cost_down
Downward reserve ramping cost for changing reserve delivery of the generator (xUnit: NO_UNIT, yUnit: NOK)


(generator:ref_production)=
### ref_production
Production of the generator indicating the planned operating point as starting point for the best profit calculation (xUnit: NO_UNIT, yUnit: MW)


(generator:schedule_deviation_flag)=
### schedule_deviation_flag
Flag determining whether the generator can deviate from the input schedule when calculating marginal cost and best profit curves. Implicitly generated based on the ref_prod attribute if the command 'set prod_from_ref_prod' is used. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:gen_turn_off_limit)=
### gen_turn_off_limit
A decimal number between 0 and 1 that signifies if the generator operates below the fraction (the decimal number) of its minimum operating limit in a full mode without MIP, the unit will be turned off. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_n_up_cost)=
### fcr_n_up_cost
The cost of allocating FCR-N up reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:fcr_n_down_cost)=
### fcr_n_down_cost
The cost of allocating FCR-N down reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:fcr_d_up_cost)=
### fcr_d_up_cost
The cost of allocating FCR-D up reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:fcr_d_down_cost)=
### fcr_d_down_cost
The cost of allocating FCR-D down reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:frr_up_cost)=
### frr_up_cost
The cost of allocating FRR up reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:frr_down_cost)=
### frr_down_cost
The cost of allocating FRR down reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:rr_up_cost)=
### rr_up_cost
The cost of allocating RR up reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:rr_down_cost)=
### rr_down_cost
The cost of allocating RR down reserves on this generator (xUnit: NO_UNIT, yUnit: NOK/MW)


(generator:spinning_reserve_up_max)=
### spinning_reserve_up_max
Sets a maximum limit for the sum of spinning reserves delivered in the upward direction on the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:spinning_reserve_down_max)=
### spinning_reserve_down_max
Sets a maximum limit for the sum of spinning reserves delivered in the downward direction on the generator (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_droop_cost)=
### fcr_n_droop_cost
The cost for the inverse unit droop for FCR-N reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. The droop_cost attribute on the generator or global_settings is used if this attribut is not specified. (xUnit: NO_UNIT, yUnit: NOK)


(generator:fcr_d_up_droop_cost)=
### fcr_d_up_droop_cost
The cost for the inverse unit droop for FCR-D up reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. The droop_cost attribute on the generator or global_settings is used if this attribut is not specified. (xUnit: NO_UNIT, yUnit: NOK)


(generator:fcr_d_down_droop_cost)=
### fcr_d_down_droop_cost
The cost for the inverse unit droop for FCR-D down reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. The droop_cost attribute on the generator or global_settings is used if this attribut is not specified. (xUnit: NO_UNIT, yUnit: NOK)


(generator:fcr_n_fixed_droop)=
### fcr_n_fixed_droop
Fixed unit droop schedule for FCR-N reserves when droop is built separately for FCR-N and FCR-D (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_up_fixed_droop)=
### fcr_d_up_fixed_droop
Fixed unit droop schedule for FCR-D up reserves when droop is built separately for FCR-N and FCR-D (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_down_fixed_droop)=
### fcr_d_down_fixed_droop
Fixed unit droop schedule for FCR-D down reserves when droop is built separately for FCR-N and FCR-D (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_n_droop_min)=
### fcr_n_droop_min
The lower bound of the unit droop for FCR-N reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. This bound is applied together with other FCR-N constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_up_droop_min)=
### fcr_d_up_droop_min
The lower bound of the unit droop for FCR-D up reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. This bound is applied together with other FCR-D up constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_down_droop_min)=
### fcr_d_down_droop_min
The lower bound of the unit droop for FCR-D down reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. This bound is applied together with other FCR-D down constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_n_droop_max)=
### fcr_n_droop_max
The upper bound of the unit droop for FCR-N reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. This bound is applied together with other FCR-N constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_up_droop_max)=
### fcr_d_up_droop_max
The upper bound of the unit droop for FCR-D up reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. This bound is applied together with other FCR-D up constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_down_droop_max)=
### fcr_d_down_droop_max
The upper bound of the unit droop for FCR-D down reserves when it is modelled as a variable in the optimization model and droop is built separately for FCR-N and FCR-D. This bound is applied together with other FCR-D down constraints, where the most restrictive will limit the FCR delivery (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:couple_fcr_delivery_flag)=
### couple_fcr_delivery_flag
If this flag is set to 1, no FCR-D capacity can be allocated to the generator unless the allocated FCR-N reserve capacity is at its maximal value. Upward and downward reserve capacity are handled separately. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:historical_production)=
### historical_production
The generator production for times before the optimization start. (xUnit: NO_UNIT, yUnit: MW)


(generator:min_uptime)=
### min_uptime
Minimum generator up-time, given in whole minutes. (xUnit: MINUTE, yUnit: MINUTE)


(generator:min_downtime)=
### min_downtime
Minimum generator down-time, given in whole minutes. (xUnit: MINUTE, yUnit: MINUTE)


(generator:min_uptime_flag)=
### min_uptime_flag
Flag for turning minimum uptime constraints on (1) or off (0). Constraints are built if no flag is given (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:min_downtime_flag)=
### min_downtime_flag
Flag for turning minimum downtime constraints on (1) or off (0). Constraints are built if no flag is given (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:rr_down_stop_mip_flag)=
### rr_down_stop_mip_flag
Setting this flag to 1 will turn on the use of binary variables in full iterations to enable this generator to deliver valid RR-DOWN reserves down to full stop. This forces RR-DOWN to either be alocated as spinning reserve (down to p_min) or down to a full stop, and no other spinning reservers can be allocated on the unit if RR-DOWN is delivered down to stop. RR-DOWN allocation in forbidden production regions (between 0 and p_min) is also prohibited. If the flag is not specified, the attribute 'rr_down_stop_mip' on global_settings is used (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:min_discharge)=
### min_discharge
Minimum discharge as a function of net head (xUnit: METER, yUnit: M3/S)


(generator:max_discharge)=
### max_discharge
Maximum discharge as a function of net head (xUnit: METER, yUnit: M3/S)


(generator:eff_head)=
### eff_head
Resulting effective head of the generator (xUnit: NO_UNIT, yUnit: METER)


(generator:sim_eff_head)=
### sim_eff_head
The simulated effective head of the generator (xUnit: NO_UNIT, yUnit: METER)


(generator:head_loss)=
### head_loss
Resulting head loss of the generator, i.e. the plant gross head (gross_head) minus the effective head of the generator (eff_head) (xUnit: NO_UNIT, yUnit: METER)


(generator:sim_head_loss)=
### sim_head_loss
Resulting head loss of the generator in the simulation, i.e. the plant gross head (gross_head) minus the effective head of the generator (eff_head) (xUnit: NO_UNIT, yUnit: METER)


(generator:production)=
### production
Resulting generator production, calculated base on discharge (xUnit: NO_UNIT, yUnit: MW)


(generator:solver_production)=
### solver_production
Preliminary result for generator production that is returned by the linearized optimization problem (xUnit: NO_UNIT, yUnit: MW)


(generator:sim_production)=
### sim_production
Simulated generator production (xUnit: NO_UNIT, yUnit: MW)


(generator:discharge)=
### discharge
Resulting generator discharge. If solver_discharge >= gen_turn_off_limit, discharge is equal to solver_discharge. Otherwise, discharge = 0. (xUnit: NO_UNIT, yUnit: M3/S)


(generator:solver_discharge)=
### solver_discharge
Preliminary result for generator discharge that is returned by the linearized optimization problem (xUnit: NO_UNIT, yUnit: M3/S)


(generator:sim_discharge)=
### sim_discharge
Simulated generator discharge (xUnit: NO_UNIT, yUnit: M3/S)


(generator:committed_out)=
### committed_out
Committed status of the generator as a result of the optimization: 0 - not running; 1 - committed to run. Note that if a Pelton is committed to run, the number of needle_comb is returned. (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:production_schedule_penalty)=
### production_schedule_penalty
Resulting penalty when the generator production schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:discharge_schedule_penalty)=
### discharge_schedule_penalty
Resulting penalty when the generator discharge schedule is violated (xUnit: NO_UNIT, yUnit: MM3)


(generator:fcr_n_up_delivery)=
### fcr_n_up_delivery
Resulting generator FCR_N_UP delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_down_delivery)=
### fcr_n_down_delivery
Resulting generator FCR_N_DOWN delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_up_delivery)=
### fcr_d_up_delivery
Resulting generator FCR_D_UP delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_down_delivery)=
### fcr_d_down_delivery
Resulting generator FCR_D_DOWN delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_up_delivery)=
### frr_up_delivery
Resulting generator FRR_UP delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_down_delivery)=
### frr_down_delivery
Resulting generator FRR_DOWN delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_up_delivery)=
### rr_up_delivery
Resulting generator RR_UP delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_down_delivery)=
### rr_down_delivery
Resulting generator RR_DOWN delivery (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_up_delivery_physical)=
### fcr_n_up_delivery_physical
Resulting physical generator FCR_N delivery in the upward direction (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_down_delivery_physical)=
### fcr_n_down_delivery_physical
Resulting physical generator FCR_N delivery in the downward direction (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_up_delivery_physical)=
### fcr_d_up_delivery_physical
Resulting physical generator FCR_D delivery in the upward direction (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_down_delivery_physical)=
### fcr_d_down_delivery_physical
Resulting physical generator FCR_D delivery in the downward direction (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_up_schedule_penalty)=
### fcr_n_up_schedule_penalty
Resulting penalty when the generator FCR_N_UP schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_down_schedule_penalty)=
### fcr_n_down_schedule_penalty
Resulting penalty when the generator FCR_N_DOWN schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_up_schedule_penalty)=
### fcr_d_up_schedule_penalty
Resulting penalty when the generator FCR_D_UP schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_d_down_schedule_penalty)=
### fcr_d_down_schedule_penalty
Resulting penalty when the generator FCR_D_DOWN schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_up_schedule_penalty)=
### frr_up_schedule_penalty
Resulting penalty when the generator FRR_UP schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:frr_down_schedule_penalty)=
### frr_down_schedule_penalty
Resulting penalty when the generator FRR_DOWN schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_up_schedule_penalty)=
### rr_up_schedule_penalty
Resulting penalty when the generator RR_UP schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:rr_down_schedule_penalty)=
### rr_down_schedule_penalty
Resulting penalty when the generator RR_DOWN schedule is violated (xUnit: NO_UNIT, yUnit: MW)


(generator:droop_result)=
### droop_result
Resulting unit droop when it is modelled as a variable in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:best_profit_q)=
### best_profit_q
Optimal discharge for the generator given a certain production level of the plant. Created after the command 'create bp_curves' has been performed (xUnit: MW, yUnit: M3/S)


(generator:best_profit_p)=
### best_profit_p
Optimal production for the generator given a certain production level of the plant. Created after the command 'create bp_curves' has been performed (xUnit: MW, yUnit: MW)


(generator:best_profit_dq_dp)=
### best_profit_dq_dp
Ratio between discharge and production for the generator given a certain production level of the plant. Created after the command 'create bp_curves' has been performed (xUnit: MW, yUnit: M3/S)


(generator:best_profit_needle_comb)=
### best_profit_needle_comb
Optimal needle combination for the generator given a certain production level of the plant. Created after the command 'create bp_curves' has been performed (xUnit: MW, yUnit: NO_UNIT)


(generator:startup_cost_mip_objective)=
### startup_cost_mip_objective
Cost in the objective function of the solver from startup costs originating from the time steps when MIP is used (xUnit: NO_UNIT, yUnit: NOK)


(generator:startup_cost_total_objective)=
### startup_cost_total_objective
Post-optimization calculated startup costs based on change in commitment status for both time steps with and without MIP activated (xUnit: NO_UNIT, yUnit: NOK)


(generator:discharge_fee_objective)=
### discharge_fee_objective
Cost in the objective function resulting from discharge fees for this generator (xUnit: NO_UNIT, yUnit: NOK)


(generator:feeding_fee_objective)=
### feeding_fee_objective
Cost in the objective function resulting from feed-in fees for this generator (xUnit: NO_UNIT, yUnit: NOK)


(generator:schedule_penalty)=
### schedule_penalty
Resulting penalty cost when the generator schedule (production schedule and/or discharge schedule) for the generator is voilated (xUnit: NO_UNIT, yUnit: NOK)


(generator:market_income)=
### market_income
Income in the objective function from selling the energy produced on this generator (xUnit: NO_UNIT, yUnit: NOK)


(generator:original_pq_curves)=
### original_pq_curves
Original PQ-curve for the generator that includes non-convex regions (xUnit: M3/S, yUnit: MW)


(generator:convex_pq_curves)=
### convex_pq_curves
Convexified PQ-curve for the generator that includes all the time-dependent operating limits and removes all the nonconcave points of the original PQ curve. The slope of each segment is non-increasing. (xUnit: M3/S, yUnit: MW)


(generator:final_pq_curves)=
### final_pq_curves
Final PQ curve for the generator that is the final form included into the optimization problem. The first point of the convex PQ curve is extended to Q=0. (xUnit: M3/S, yUnit: MW)


(generator:max_prod_individual)=
### max_prod_individual
The head dependent maximal production of the generator if all other units continue to operate at their current production level, most accurate in incremental iterations (xUnit: NO_UNIT, yUnit: MW)


(generator:max_prod_all)=
### max_prod_all
The head dependent maximal production of the generator if all generators not on maintenance in the plant are also producing at maximum (xUnit: NO_UNIT, yUnit: MW)


(generator:max_prod_available)=
### max_prod_available
The head dependent maximal production of the generator if all generators not on maintenance or committed off in the plant are also producing at maximum (xUnit: NO_UNIT, yUnit: MW)


(generator:max_prod_spinning)=
### max_prod_spinning
The head dependent maximal production of the generator if all spinning generators in the plant are also producing at maximum (xUnit: NO_UNIT, yUnit: MW)


(generator:min_prod_individual)=
### min_prod_individual
The head dependent minimal production of the generator if all other units continue to operate at their current production level, most accurate in incremental iterations (xUnit: NO_UNIT, yUnit: MW)


(generator:min_prod_spinning)=
### min_prod_spinning
The head dependent minimal production of the generator if all spinning generators in the plant are also producing at minimum (xUnit: NO_UNIT, yUnit: MW)


(generator:fcr_n_droop_result)=
### fcr_n_droop_result
The optimized unit droop for FCR-N reserves when the droop is built separately for FCR-N and FCR-D. If all FCR reserves share a common droop setting, this txy is identical to the 'droop_result' attribute (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_up_droop_result)=
### fcr_d_up_droop_result
The optimized unit droop for FCR-D up reserves when the droop is built separately for FCR-N and FCR-D. If all FCR reserves share a common droop setting, this txy is identical to the 'droop_result' attribute (xUnit: NO_UNIT, yUnit: NO_UNIT)


(generator:fcr_d_down_droop_result)=
### fcr_d_down_droop_result
The optimized unit droop for FCR-D down reserves when the droop is built separately for FCR-N and FCR-D. If all FCR reserves share a common droop setting, this txy is identical to the 'droop_result' attribute (xUnit: NO_UNIT, yUnit: NO_UNIT)